In [2]:
import torch
import torch.nn as nn
import torch.optim as optim
from torch.utils.data import DataLoader, Dataset
from collections import Counter
from sklearn.model_selection import train_test_split

from torchtext.vocab import vocab
from tqdm.notebook import tqdm
import pandas as pd
import numpy as np

# Funkcja do wczytywania danych
def load_datasets():
    train_df = pd.read_csv(
        "train/train.tsv.xz", compression="xz", sep="\t", names=["Category", "Sentence"]
    )
    dev_df = pd.read_csv("dev-0/in.tsv", sep="\t", names=["Sentence"])
    dev_labels = pd.read_csv("dev-0/expected.tsv", sep="\t", names=["Category"])
    test_df = pd.read_csv("test-A/in.tsv", sep="\t", names=["Sentence"])
    return train_df, dev_df, dev_labels, test_df

train_df, dev_df, dev_labels, test_df = load_datasets()
train_texts, val_texts, train_labels, val_labels = train_test_split(
    train_df["Sentence"], train_df["Category"], test_size=0.1, random_state=42
)
train_df = pd.DataFrame({"Sentence": train_texts, "Category": train_labels})
val_df = pd.DataFrame({"Sentence": val_texts, "Category": val_labels})

# Tokenizacja danych
train_df["tokens"] = train_df["Sentence"].apply(lambda x: x.split())
train_df["label_tokens"] = train_df["Category"].apply(lambda x: x.split())
test_df["tokens"] = test_df["Sentence"].apply(lambda x: x.split())
val_df["tokens"] = val_df["Sentence"].apply(lambda x: x.split())
val_df["label_tokens"] = val_df["Category"].apply(lambda x: x.split())
dev_df["tokens"] = dev_df["Sentence"].apply(lambda x: x.split())
dev_df["label_tokens"] = dev_labels["Category"].apply(lambda x: x.split())

# Budowanie słownika
def create_vocab(token_list):
    count = Counter()
    for tokens in token_list:
        count.update(tokens)
    return vocab(count, specials=["<unk>", "<pad>", "<bos>", "<eos>"])

vocabulary = create_vocab(train_df["tokens"])
index_to_string = vocabulary.get_itos()
print(index_to_string)
print(len(index_to_string))

vocabulary.set_default_index(vocabulary["<unk>"])

# Przetwarzanie danych na wektory
def vectorize_data(data_tokens):
    return [
        torch.tensor([vocabulary["<bos>"]] + [vocabulary[token] for token in tokens] + [vocabulary["<eos>"]], dtype=torch.long)
        for tokens in data_tokens
    ]

def vectorize_labels(data_labels, label_map):
    return [
        torch.tensor([0] + [label_map[label] for label in labels] + [0], dtype=torch.long, device=device)
        for labels in data_labels
    ]

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
train_tokens = vectorize_data(train_df["tokens"])
test_tokens = vectorize_data(test_df["tokens"])
val_tokens = vectorize_data(val_df["tokens"])
dev_tokens = vectorize_data(dev_df["tokens"])

label_list = ["O", "B-PER", "I-PER", "B-ORG", "I-ORG", "B-LOC", "I-LOC", "B-MISC", "I-MISC"]
label_map = {label: idx for idx, label in enumerate(label_list)}

train_label_tokens = vectorize_labels(train_df["label_tokens"], label_map)
val_label_tokens = vectorize_labels(val_df["label_tokens"], label_map)
dev_label_tokens = vectorize_labels(dev_df["label_tokens"], label_map)

# Funkcja do obliczania metryk
def calculate_metrics(true_labels, pred_labels):
    accuracy = 0
    true_positive = 0
    false_positive = 0
    total_selected = 0
    total_relevant = 0

    for pred, true in zip(pred_labels, true_labels):
        if pred == true:
            accuracy += 1

        if pred > 0 and pred == true:
            true_positive += 1

        if pred > 0:
            total_selected += 1

        if true > 0:
            total_relevant += 1

    precision = true_positive / total_selected if total_selected > 0 else 1.0
    recall = true_positive / total_relevant if total_relevant > 0 else 1.0
    f1_score = 2 * precision * recall / (precision + recall) if (precision + recall) > 0 else 0.0

    return precision, recall, f1_score

label_indices = [label_map[label] for labels in train_df["label_tokens"] for label in labels]
num_classes = max(label_indices) + 1
print(num_classes)

# Definicja modelu LSTM
class BiLSTM(nn.Module):
    def __init__(self, vocab_size, embed_dim, hidden_dim, num_layers, num_classes):
        super(BiLSTM, self).__init__()
        self.embedding = nn.Embedding(vocab_size, embed_dim)
        self.lstm = nn.LSTM(embed_dim, hidden_dim, num_layers, batch_first=True, bidirectional=True)
        self.fc = nn.Linear(hidden_dim * 2, num_classes)

    def forward(self, x):
        x_embed = torch.relu(self.embedding(x))
        lstm_out, _ = self.lstm(x_embed)
        logits = self.fc(lstm_out)
        return logits

model = BiLSTM(len(index_to_string), 100, 100, 1, num_classes).to(device)
loss_function = nn.CrossEntropyLoss()
optimizer = optim.Adam(model.parameters())

# Funkcja do ewaluacji modelu
def evaluate_model(data_tokens, data_labels, model):
    true_labels = []
    pred_labels = []
    for i in tqdm(range(len(data_labels))):
        tokens = data_tokens[i].unsqueeze(0)
        true_labels_batch = list(data_labels[i].cpu().numpy())
        true_labels += true_labels_batch

        pred_logits = model(tokens).squeeze(0)
        pred_batch = torch.argmax(pred_logits, 1)
        pred_labels += list(pred_batch.cpu().numpy())

    return calculate_metrics(true_labels, pred_labels)

# Funkcja do predykcji etykiet
def predict_labels(data_tokens, model, label_map):
    pred_labels = []
    inv_label_map = {v: k for k, v in label_map.items()}

    for i in tqdm(range(len(data_tokens))):
        tokens = data_tokens[i].unsqueeze(0)
        pred_logits = model(tokens).squeeze(0)
        pred_batch = torch.argmax(pred_logits, 1)
        pred_label_list = [inv_label_map[label.item()] for label in pred_batch]
        pred_label_list = pred_label_list[1:-1]
        pred_labels.append(" ".join(pred_label_list))

    return pred_labels

# Trening modelu
EPOCHS = 5
for epoch in range(EPOCHS):
    model.train()
    for i in tqdm(range(len(train_label_tokens))):
        tokens = train_tokens[i].unsqueeze(0)
        true_labels = train_label_tokens[i].unsqueeze(1)

        pred_labels = model(tokens)
        optimizer.zero_grad()
        loss = loss_function(pred_labels.squeeze(0), true_labels.squeeze(1))
        loss.backward()
        optimizer.step()

    model.eval()
    print(evaluate_model(val_tokens, val_label_tokens, model))

# Ewaluacja na zbiorze walidacyjnym i deweloperskim
evaluate_model(val_tokens, val_label_tokens, model)
evaluate_model(dev_tokens, dev_label_tokens, model)

# Generowanie predykcji dla zbiorów testowych
dev_predictions = predict_labels(dev_tokens, model, label_map)
dev_predictions_df = pd.DataFrame(dev_predictions, columns=["Category"])
dev_predictions_df.to_csv("dev-0/out.tsv", index=False, header=False)

test_predictions = predict_labels(test_tokens, model, label_map)
test_predictions_df = pd.DataFrame(test_predictions, columns=["Category"])
test_predictions_df.to_csv("test-A/out.tsv", index=False, header=False)


['<unk>', '<pad>', '<bos>', '<eos>', 'SOCCER', '-', 'POLISH', 'FIRST', 'DIVISION', 'RESULTS', '.', '</S>', 'WARSAW', '1996-08-24', 'Results', 'of', 'Polish', 'first', 'division', 'soccer', 'matches', 'on', 'Saturday', ':', 'Amica', 'Wronki', '3', 'Hutnik', 'Krakow', '0', 'Sokol', 'Tychy', '5', 'Lech', 'Poznan', 'Rakow', 'Czestochowa', '1', 'Stomil', 'Olsztyn', '4', 'Wisla', 'Gornik', 'Zabrze', 'Slask', 'Wroclaw', 'Odra', 'Wodzislaw', 'GKS', 'Katowice', 'Polonia', 'Warsaw', 'Zaglebie', 'Lubin', '2', 'LKS', 'Lodz', 'Legia', 'Belchatow', 'CRICKET', 'POLLOCK', 'CONCLUDES', 'WARWICKSHIRE', 'CAREER', 'WITH', 'FLOURISH', 'LONDON', '1996-08-25', 'South', 'African', 'fast', 'bowler', 'Shaun', 'Pollock', 'concluded', 'his', 'Warwickshire', 'career', 'with', 'a', 'flourish', 'Sunday', 'by', 'taking', 'the', 'final', 'three', 'wickets', 'during', 'county', "'s", 'league', 'victory', 'over', 'Worcestershire', ',', 'who', 'returns', 'home', 'Tuesday', 'for', 'an', 'ankle', 'operation', 'took', 'last

  0%|          | 0/850 [00:00<?, ?it/s]

  0%|          | 0/95 [00:00<?, ?it/s]

(0.5546171171171171, 0.2832901926948519, 0.37502379592613744)


  0%|          | 0/850 [00:00<?, ?it/s]

...

(0.5790436970944864, 0.727926373310325, 0.6450050968399592)


  0%|          | 0/95 [00:00<?, ?it/s]

  0%|          | 0/215 [00:00<?, ?it/s]

  0%|          | 0/215 [00:00<?, ?it/s]

  0%|          | 0/230 [00:00<?, ?it/s]